In [5]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.metrics import accuracy_score, f1_score


In [14]:
#Preprocessing train.csv
data = pd.read_csv('train.csv')

#B. feature elimination
newData = data.drop(['Name', 'PassengerId', 'Ticket', 'Cabin'],axis=1)

#A. Train-Test data split
def train_test_split(dataset):
    training_data = dataset.iloc[:600].reset_index(drop=True)
    testing_data = dataset.iloc[600:].reset_index(drop=True)
    return training_data,testing_data

training_data = train_test_split(newData)[0]
testing_data = train_test_split(newData)[1]


#C. Remove data with missing values from training & test data
train_data_b4 = pd.DataFrame(training_data)
train_data_b4.dropna(inplace=True)
test_data_b4 = pd.DataFrame(testing_data)
test_data_b4.dropna(inplace=True)

In [24]:
# Change into numerical value
dfCompile = [train_data_b4, test_data_b4]

sex_map = {"male":0, "female":1}
embark_map = {"S":0, "C":1,"Q":2}

train_data = train_data_b4.copy()
train_data['Sex'] = train_data['Sex'].map(sex_map)
train_data['Embarked'] = train_data['Embarked'].map(embark_map)

test_data = test_data_b4.copy()
test_data['Sex'] = test_data['Sex'].map(sex_map)
test_data['Embarked'] = test_data['Embarked'].map(embark_map)

for dataset in dfCompile:    
    dataset.loc[ dataset['Age'] <= 16, 'Age'] = 0
    dataset.loc[(dataset['Age'] > 16) & (dataset['Age'] <= 32), 'Age'] = 1
    dataset.loc[(dataset['Age'] > 32) & (dataset['Age'] <= 48), 'Age'] = 2
    dataset.loc[(dataset['Age'] > 48) & (dataset['Age'] <= 64), 'Age'] = 3
    dataset.loc[ dataset['Age'] > 64, 'Age']

for dataset in dfCompile:
    dataset["Age"] = dataset.groupby(dataset.Pclass).Age.transform(lambda x: x.fillna(x.median()))

In [50]:
X_train = train_data.drop(["Survived"], axis=1)
Y_train = train_data["Survived"] #labels

X_test  = test_data.drop(["Survived"], axis=1)

In [105]:
# K-Nearest Neighbors(KNN)
from sklearn.neighbors import KNeighborsClassifier
print("\t", end = "")
print("[test-acc]", end="")
print("[test-f1]")

test_data_label = test_data["Survived"] # index row, which is the answer for test data(=survived)

for i in range(2,6):
    knn = KNeighborsClassifier(n_neighbors=i)
    knn.fit(X_test, test_data_label)
    y_predict = knn.predict(X_test)
    
    # Score 
    knn_acc = accuracy_score(test_data_label, y_predict) *100
    knn_f1 = f1_score(test_data_label, y_predict) *100
    
    print("[k : %d]" %i, end = " ")
    print("  %.2f  " % knn_acc, end ="")
    print("    %.2f  " % knn_f1) 

	[test-acc][test-f1]
[k : 2]   87.03      80.00  
[k : 3]   89.12      85.23  
[k : 4]   84.94      77.78  
[k : 5]   82.43      77.66  


In [109]:
# Logistic Regression
from sklearn.linear_model import LogisticRegression
print("\t\t", end = "")
print("[Accuracy]", end = "")
print("[F1 score]")

for i in range(20,120,20):
    logit = LogisticRegression(max_iter = i)
     # CASE 1: CHANGING ITERATION NUMBER
    logit.fit(X_train, Y_train)
    y_predict = logit.predict(X_test)
    accuracy = round(logit.score(X_train, Y_train) * 100, 2)
    logit_f1 = f1_score(y_predict, test_data_label)
    print("[%d th iteration]" %i, end = " ")
    print("  %.2f  " % accuracy, end ="") 
    print("  %.2f  " % (logit_f1 * 100)) 
    
print("================================================================")
print("\t\t\t\t", end = "")
print("[Accuracy]", end = "")
print("[F1 score]")

#CASE 2: CHANGING THE REGULARIZATION STRENGTH(C)
for j in range(1,6):
        log_reg_strength = LogisticRegression(max_iter = 100, C=j)
        log_reg_strength.fit(X_train, Y_train)
        y_predict=log_reg_strength.predict(X_test)
        acc_reg_str= accuracy_score(y_predict, test_data_label) *100
        log_reg_strength_f1 = f1_score(y_predict, test_data_label)
        print("[Regularization Strength(C: %d)]" % j, end = "")
        print("  %.2f  " % acc_reg_str, end ="") 
        print("    %.2f  " % (log_reg_strength_f1 * 100)) 

		[Accuracy][F1 score]
[20 th iteration]   79.07    69.01  
[40 th iteration]   79.07    68.21  
[60 th iteration]   79.07    69.01  
[80 th iteration]   79.07    68.21  
[100 th iteration]   79.07    68.21  
				[Accuracy][F1 score]
[Regularization Strength(C: 1)]  76.99      68.21  
[Regularization Strength(C: 2)]  76.99      68.21  
[Regularization Strength(C: 3)]  76.99      68.21  
[Regularization Strength(C: 4)]  76.99      68.21  
[Regularization Strength(C: 5)]  76.99      68.21  


/Users/jominjae/opt/anaconda3/envs/model01/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/Users/jominjae/opt/anaconda3/envs/model01/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stab

In [72]:
# Decision Tree
from sklearn.tree import DecisionTreeClassifier
dt= DecisionTreeClassifier(criterion='entropy')
dt.fit(X_train, Y_train)
train_predict = dt.predict(X_train)
test_predict = dt.predict(X_test)

print("Train accuracy : %.3f" %(dt.score(X_train, Y_train)*100))
print("Train F1_score : %.3f" %(f1_score(y_predict, test_data_label)*100))
print("Test accuracy : %.3f" %(accuracy_score(test_predict, test_data_label)*100))
print("Test F1_score : %.3f" %(f1_score(test_predict, test_data_label)*100))

Train data set accuracy : 91.543
Train data set F1_Score : 68.208
Test data set accuracy : 76.151
Test data set F1_Score : 66.272


In [73]:
feature = []
train_data_feature = train_data.iloc[:, 1:7].values
for i in train_data_feature:
  feature.append(i)

fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 10), dpi=1800)

from sklearn import tree
tree.plot_tree(dt, feature_names=feature, class_names="Survived", filled=True)


[Text(0.5851897689768977, 0.9782608695652174, '[ 1.      1.      0.      1.      0.     71.2833] <= 0.5\nentropy = 0.978\nsamples = 473\nvalue = [278, 195]\nclass = S'),
 Text(0.3650990099009901, 0.9347826086956522, '[ 1.      0.      0.      0.      0.     51.8625] <= 15.875\nentropy = 0.723\nsamples = 294\nvalue = [235, 59]\nclass = S'),
 Text(0.17037953795379537, 0.8913043478260869, '[ 1.      0.      0.      0.      0.     51.8625] <= 13.25\nentropy = 0.596\nsamples = 166\nvalue = [142, 24]\nclass = S'),
 Text(0.15717821782178218, 0.8478260869565217, '[ 1.      0.      0.      0.      0.     51.8625] <= 7.742\nentropy = 0.622\nsamples = 155\nvalue = [131, 24]\nclass = S'),
 Text(0.07920792079207921, 0.8043478260869565, '[ 1.      0.      0.      0.      0.     51.8625] <= 7.227\nentropy = 0.384\nsamples = 40\nvalue = [37, 3]\nclass = S'),
 Text(0.066006600660066, 0.7608695652173914, '[ 1.      0.      0.      0.      0.     51.8625] <= 7.133\nentropy = 0.559\nsamples = 23\nvalue = 

In [111]:
from sklearn.ensemble import BaggingClassifier
print("\t", end = "  ")
print("[Train-Accuracy]", end = "")
print("[Train-F1]", end = "")
print("[Test-Accuracy]", end = "")
print("[Test-F1]")

for i in range(1, 6):
    bt = BaggingClassifier(base_estimator=DecisionTreeClassifier(), n_estimators= i)
    bt.fit(X_train, Y_train)
    predict_train = bt.predict(X_train)
    predict_Xtest = bt.predict(X_test)
    print("[bag:%d]" %i, end="")
    print("    %.2f\t  " % (accuracy_score(predict_train, Y_train)*100), end ="") #remember Y_train contains only the label!!!
    print("  %.2f       " % (f1_score(predict_train, Y_train)*100), end ="")
    print("  %.2f    " % (accuracy_score(predict_Xtest, test_data_label)*100), end ="")
    print("    %.2f  " % (f1_score(predict_Xtest, test_data_label) * 100))

	  [Train-Accuracy][Train-F1][Test-Accuracy][Test-F1]
[bag:1]    88.16	    85.26         77.41        69.66  
[bag:2]    84.78	    78.70         75.73        62.34  
[bag:3]    89.64	    86.72         76.15        67.43  
[bag:4]    88.16	    84.44         79.08        69.88  
[bag:5]    90.70	    87.91         79.50        70.66  
